# Approach 1:

### LOADING IN LIBRARIES

In [ ]:
#LOADING IN THE LIBRARIES
#for obtaining individual events or related
import obspy as op
import numpy as np
import cartopy.crs as ccrs
from obspy.clients.fdsn import Client
import cartopy.feature as cfeature

import cartopy
import cartopy.mpl.geoaxes
from mpl_toolkits.axes_grid1.inset_locator import inset_axes

import matplotlib.pyplot as plt
%matplotlib inline
%config InlineBackend.figure_format = 'retina'

import datetime

#Display the graphics outside of the notebook
#%matplotlib osx


### TO PRODUCE ANIMATION OF EARTHQUAKE DISTRIBUTION:

In [ ]:
currentDT = datetime.datetime.now()
print ('Download initiated. Took 1 min, but requires an internet connection.')
print ('Download began: ',str(currentDT))

client = Client("IRIS")

minLat = -40
maxLat = -30
minLon = -78
maxLon = -69 


for e in range(2,29): 
    #range is 2 to 29 (exclusive) b/c catalog begins on day 1
    
    if e < 10:
         e = str(e).zfill(2) #converts numbers from '1' to '01'
    else:
        e = str(e)

    #Capturing Feb 1- Feb 28, 2010 to capture foreshock and aftershocks after 
    #the Feb 27 Maule Earthquake (8.8)
    t1 = op.UTCDateTime("2010-02-01T00:00:00") #start time of the request
    t2 = op.UTCDateTime("2010-02-"+str(e)+"T23:59:59") #end time of the request
    
    minMag = 4.0
    
    # read https://docs.obspy.org/packages/autogen/obspy.clients.fdsn.client.Client.get_events.html
    catalog = client.get_events(starttime=t1, endtime=t2, minlatitude = minLat, 
                                maxlatitude = maxLat, 
                                minlongitude = minLon, maxlongitude = maxLon, 
                                minmagnitude=minMag)

    plt.gcf()
    plt.rcParams['figure.figsize'] = [13, 9]
    catalog.plot(projection="local",colormap = 'inferno',method = 'cartopy',outfile = 'ChileDay_'+e+'.png')
    #plt.show()
    #compiled animation by combining png files into an mp4

    plt.draw()
    
currentDT = datetime.datetime.now()
print ('Download ended: ',str(currentDT))

### TO PRODUCE STILL IMAGES OF EARTHQUAKE DISTRIBUTION

In [ ]:
#CREATE A CATALOG WITH EVENTS OF INTEREST

currentDT = datetime.datetime.now()
print ('Download initiated. Should take less than a minute, but requires an internet connection.')
print ('Download began: ',str(currentDT))

client = Client("IRIS")

minLat = -40#-57
maxLat = -30#-17
minLon = -78#270
maxLon = -69 #293

#Capturing Feb 1- Feb 28, 2010 to capture foreshock and aftershocks after 
#the Feb 27 Maule Earthquake (8.8)
t1 = op.UTCDateTime("2010-02-01T00:00:00") #start time of the request
t2 = op.UTCDateTime("2010-02-28T23:59:59") #end time of the request

minMag = 4.0

# read https://docs.obspy.org/packages/autogen/obspy.clients.fdsn.client.Client.get_events.html
catalog = client.get_events(starttime=t1, endtime=t2, minlatitude = minLat, 
                            maxlatitude = maxLat, 
                            minlongitude = minLon, maxlongitude = maxLon, 
                            minmagnitude=minMag)

currentDT = datetime.datetime.now()
print ('Download ended: ',str(currentDT))

In [ ]:
#PRINTING HERE- MAKING SURE INDEXING CATALOG WORKS

# print(catalog)
# print(len(catalog.events))
# print(catalog[0].origins[0].latitude,catalog[0].origins[0].longitude)
# print(catalog[0].origins[0].time)
# print(catalog[0].magnitudes[0].mag)
# print(type(catalog))

In [ ]:
#EXTRACT CATALOG ELEMENTS INTO LARGE EVENT RELATED LISTS
#AND MAIN SHOCK ELEMENTS

evlat =[]
evlon =[]
evdep =[] #in km
evmag = [] #magnitude raised to an exponent to be visible on plot
index = 0
emag = [] #magnitude without exponent (between 4.0 - 10.0 with current inquiry)
evot = [] #event time/ origin time


for eve in catalog:
    event = catalog[index]
    org = event.origins
    evlat.append(float(org[0].latitude))
    evlon.append(float(org[0].longitude))
    evot.append(org[0].time)
    #print(org[0].depth)
    if (org[0].depth==None):
        evdep.append(0.0)
    else:
        evdep.append((float(org[0].depth)) / 1000.0)
    evmag.append((float(event.magnitudes[0].mag))**4/2)
    emag.append(float(event.magnitudes[0].mag))
            
    if (emag[index] == 8.8):
        print(index) #reveals the index value of the large Maule EQ
        big1 = index #saving the index value under big1
        
        #finding individual values of Maule EQ to plot later
        biglat = catalog[big1].origins[0].latitude #Maule lat
        biglon = catalog[big1].origins[0].longitude #Maule lon
        bigdep = (catalog[big1].origins[0].depth) / 1000 #Maule depth in km
        bigmagexp = (catalog[big1].magnitudes[0].mag)**4/2 #Maule magnitude raised to exp for visibility
        bigmag = catalog[big1].magnitudes[0].mag #Maule magnitude without exponent
        bigot = catalog[big1].origins[0].time
    index+=1
    last = index

In [ ]:
#prints all the entries in catalog
#print(catalog.__str__(print_all=True))

print(big1) #index of the big Maule EQ
print(last) #this is the last index value

#bigone = catalog[big1]
#print(bigone)

#verifying print statements match information in bigone -- success
print(biglat,biglon,bigdep,bigmagexp, bigmag,bigot)


#CREATING SMALLER LISTS FOR FORESHOCKS AND AFTERSHOCKS

#Before the main shock lists
b4lat = []
b4lon = []
b4dep =[] #in km
b4magexp = [] #magnitude raised to an exponent to be visible on plot
b4mag = [] #magnitude without exponent (Richter Scale)
b4ot = [] #event time/ origin time

#After the main shock lists
aflat = []
aflon = []
afdep =[] #in km
afmagexp = [] #magnitude raised to an exponent to be visible on plot
afmag = [] #magnitude without exponent (Richter Scale)
afot = [] #event time/ origin time

for i in range (last):
    if i < big1 : #catalog has events ordered recent to old, i>big1 = aftershocks
        aflat.append(evlat[i])
        aflon.append(evlon[i])
        afdep.append(evdep[i])
        afmagexp.append(evmag[i])
        afmag.append(emag[i])
        afot.append(evot[i])
    if i > big1: #catalog has events ordered recent to old, i<big1 = foreshocks
        b4lat.append(evlat[i])
        b4lon.append(evlon[i])
        b4dep.append(evdep[i])
        b4magexp.append(evmag[i])
        b4mag.append(emag[i])
        b4ot.append(evot[i])

### Plotting still images

In [ ]:

fig= plt.figure(figsize=(13,9),dpi = 100)
ax = fig.add_subplot(1,1,1, projection=ccrs.PlateCarree())
ax.set_extent([minLon,maxLon,minLat,maxLat], crs=ccrs.PlateCarree())
ax.set_extent([-78,-69,-40,-30], crs=ccrs.PlateCarree()) #this extent is different from dimensions in catalog


# Plot before/ foreshocks
ib = ax.scatter(b4lon, b4lat,
                s=b4magexp,
                # c=b4mag, 
                edgecolors = 'm', 
                linewidths = 4.0, 
                transform=ccrs.PlateCarree(),marker = 'p',
                label = 'Earthquakes Before February 27', 
                alpha=0.5, cmap='inferno')



# Plot the main shock
ax.scatter(biglon, biglat, s= bigmagexp,
           # c=bigdep,
           # s=1500, 
           transform=ccrs.PlateCarree(),#marker = '*',
           edgecolors = 'r',
           linewidths = 4.0,
           label = 'Maule Chile Earthquake (27 February, 2010)',
           alpha=0.75,
           cmap='inferno')

#Plot features
ax.gridlines(draw_labels=True, dms=True)
ax.add_feature(cfeature.LAND, facecolor='grey')
ax.add_feature(cfeature.OCEAN)
ax.add_feature(cfeature.BORDERS, linestyle=':',linewidth = 5.0)
ax.set_title("Earthquakes Before Maule 2010 (Feb 2-Feb 27)")

plt.legend(loc='upper left')

#plotting the inset (mini globe) figure
axins = inset_axes(ax, width="50%", height="50%", loc="center left", 
                  axes_class=cartopy.mpl.geoaxes.GeoAxes, 
                  axes_kwargs=dict(projection=cartopy.crs.Orthographic(central_longitude = 280,
                                                                          central_latitude = -30)))
axins.set_global()
axins.add_feature(cfeature.COASTLINE)
axins.add_feature(cfeature.LAND)
axins.add_feature(cfeature.OCEAN)
axins.add_feature(cfeature.BORDERS)
axins.plot([minLon,minLon,maxLon,maxLon, minLon],[minLat,maxLat,maxLat,minLat,minLat], 
transform = ccrs.Geodetic(),c= 'r') #plots the red square in inset figure
axins.set_global()


plt.draw()

#plt.savefig('Chile_Before_still.png')

In [ ]:
fig= plt.figure(figsize=(13,9),dpi = 100)
ax = fig.add_subplot(1,1,1, projection=ccrs.PlateCarree())
ax.set_extent([minLon,maxLon,minLat,maxLat], crs=ccrs.PlateCarree())
ax.set_extent([-78,-69,-40,-30], crs=ccrs.PlateCarree()) #this extent is different from dimensions in catalog



# Plot after/ aftershocks
ax.scatter(aflon, aflat, s=afmagexp,  
           # c=afdep,
           edgecolors = 'c', 
           linewidths = 4.0, 
           transform=ccrs.PlateCarree(),marker = 's',
           label = 'Earthquakes After Maule 2010', 
           alpha=0.5, cmap='inferno')

# Plot the main shock
ax.scatter(biglon, biglat, s= bigmagexp,
           # c=bigdep,
           # s=1500, 
           transform=ccrs.PlateCarree(),#marker = '*',
           edgecolors = 'r',
           linewidths = 4.0,
           label = 'Maule Chile Earthquake (27 February, 2010)',
           alpha=0.75,
           cmap='inferno')

#Plot features
ax.gridlines(draw_labels=True, dms=True)
ax.add_feature(cfeature.LAND, facecolor='grey')
ax.add_feature(cfeature.OCEAN)
ax.add_feature(cfeature.BORDERS, linestyle=':',linewidth = 5.0)
ax.set_title("Earthquakes After Maule 2010 (Feb 2-Feb 27)")

plt.legend(loc='upper left')#, bbox_to_anchor=(0.5, 0.05),fontsize=25)

#plotting the inset (mini globe) figure
axins = inset_axes(ax, width="40%", height="40%", loc="center left", 
                  axes_class=cartopy.mpl.geoaxes.GeoAxes, 
                  axes_kwargs=dict(projection=cartopy.crs.Orthographic(central_longitude = 280,
                                                                          central_latitude = -30)))
axins.set_global()
axins.add_feature(cfeature.COASTLINE)
axins.add_feature(cfeature.LAND)
axins.add_feature(cfeature.OCEAN)
axins.add_feature(cfeature.BORDERS)
axins.plot([minLon,minLon,maxLon,maxLon, minLon],[minLat,maxLat,maxLat,minLat,minLat], 
transform = ccrs.Geodetic(),c= 'r') #plots the red square in inset figure
axins.set_global()


plt.draw()

# plt.savefig('Chile_After_still.png')

In [ ]:

fig= plt.figure(figsize=(13,9),dpi = 100)
ax = fig.add_subplot(1,1,1, projection=ccrs.PlateCarree())
ax.set_extent([minLon,maxLon,minLat,maxLat], crs=ccrs.PlateCarree())
ax.set_extent([-78,-69,-40,-30], crs=ccrs.PlateCarree()) #this extent is different from dimensions in catalog


# Plot after
ax.scatter(aflon, aflat, s=afmag,  
           #c=afdep,
           edgecolors = 'c', 
           linewidths = 4.0, 
           transform=ccrs.PlateCarree(),marker = 's',
           label = 'Earthquakes After Maule 2010', 
           alpha=0.5, cmap='inferno')


# Plot before
ax.scatter(b4lon, b4lat,
                s=b4mag,
                # c=b4mag, 
                edgecolors = 'm', 
                linewidths = 4.0, 
                transform=ccrs.PlateCarree(),marker = 'p',
                label = 'Earthquakes Before Maule 2010', 
                alpha=0.5, cmap='inferno')
# Plot the main shock
ax.scatter(biglon, biglat, s= bigmag,
           # c=bigdep,
           # s=1500, 
           transform=ccrs.PlateCarree(),#marker = '*',
           edgecolors = 'r',
           linewidths = 4.0,
           label = 'Maule Chile Earthquake (27 February, 2010)',
           alpha=0.75,
           cmap='inferno')


#Plot features
ax.gridlines(draw_labels=True, dms=True)
ax.add_feature(cfeature.LAND, facecolor='grey')
ax.add_feature(cfeature.OCEAN)
ax.add_feature(cfeature.BORDERS, linestyle=':',linewidth = 5.0)
ax.set_title("Earthquakes Before and After Maule 2010")

plt.legend(loc='upper left')

#plotting the inset (mini globe) figure
axins = inset_axes(ax, width="40%", height="40%", loc="center left", 
                  axes_class=cartopy.mpl.geoaxes.GeoAxes, 
                  axes_kwargs=dict(projection=cartopy.crs.Orthographic(central_longitude = 280,
                                                                          central_latitude = -30)))
axins.set_global()
axins.add_feature(cfeature.COASTLINE)
axins.add_feature(cfeature.LAND)
axins.add_feature(cfeature.OCEAN)
axins.add_feature(cfeature.BORDERS)
axins.plot([minLon,minLon,maxLon,maxLon, minLon],[minLat,maxLat,maxLat,minLat,minLat], 
transform = ccrs.Geodetic(),c= 'r') #plots the red square in inset figure
axins.set_global()


plt.draw()

#plt.savefig('Chile_Final_still.png')